In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import altair as alt
import warnings
warnings.simplefilter(action='ignore', category=pd.errors.SettingWithCopyWarning)
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

# Rent Prices Pre- and Post- COVID (Faceted Plot)

In [ ]:
df = pd.read_csv('data/apts_combined.csv', dtype={'zipcode': 'object'})

In [ ]:
df.head()

In [ ]:
df.info()

In [ ]:
df["cityname"] = df["cityname"].astype(str)
df["state"] = df["state"].astype(str)

In [ ]:
alt.data_transformers.enable("vegafusion")

In [ ]:
alt.Chart(df).mark_bar().encode(
        alt.X("price:Q", bin=alt.Bin(maxbins=25), title="Monthly Rent ($)"),
        alt.Y("percent:Q", axis=alt.Axis(format=".0f", title="Percentage of rentals (%)")),
        alt.Color("year:N", title="Year", legend=None)
).transform_joinaggregate(
        total='count()',
        groupby=['year']
).transform_calculate(
        percent='(1 / datum.total) * 100'
).facet(
        column=alt.Column("year:N", title=' ',
                          header=alt.Header(labelFontSize=14, labelFontWeight="bold",))
).properties(
        title="Pre- vs Post-COVID Rent Prices for Apartments Across the USA"
).configure_title(
    anchor='middle'
)

In [ ]:
box = (
    alt.Chart(df)
    .mark_boxplot()
    .encode(
        x=alt.X("year:N", title="Year"),
        y=alt.Y("price:Q", title="Monthly Rent ($)")
    )
    .properties(height=150)
)

density = (
    alt.Chart(df)
    .transform_density(
        "price",
        groupby=["year"],
        as_=["price", "density"]
    )
    .mark_area(opacity=0.4)
    .encode(
        x=alt.X("price:Q", title="Monthly Rent ($)"),
        y=alt.Y("density:Q", title="Density"),
        color=alt.Color("year:N", title="Year")
    )
    .properties(height=150)
)

chart_compound = alt.hconcat(box, density).properties(
    title="Price Levels and Variability (2019 vs 2025)"
)

In [ ]:
chart_compound

# Merging Data For State to State Comparison

In [2]:
df = pd.read_csv('apts_2019_clean.csv') #2019 data

df_scraped = pd.read_csv('apts_2025_clean.csv') #2025 data

df_scraped = df_scraped.rename(columns={'zpid':'id'}) #Rename column to merge
#Add in columns that exist within 2019 data but not 2025 data to be able to merge easier
for col_name in df.columns[~df.columns.isin(df_scraped.columns)]:
    df_scraped[col_name] = np.nan
    
df_scraped["year"] = '2025' #Add year label to scraped data

df_sub = df.loc[df['state'].isin(df_scraped['state']),:] #Keep only states found in both datasets
df_sub["year"] = "2019" #Add year label for 2019 data
df_sub.reset_index(drop=True, inplace=True)

df_all = pd.concat([df_sub, df_scraped], ignore_index=True) #Merge

# Percent Rent Increase by State (Choropleth and Bar Plot)

In [3]:
#How did average apartment price increase from 2019 to 2025 for each state
#Which states have greatest increase in mean apartment price from 2019 to 2025
#Further analysis (not shown in this code) considered median values as well, but since outliers were removed, went ahead with mean
df_2025 = df_all.loc[df_all["year"] == "2025", ["state","price"]].groupby("state").agg(["count","mean"])
df_2019 = df_all.loc[df_all["year"] == "2019", ["state","price"]].groupby("state").agg(["count","mean"])

df_2025.columns = df_2025.columns.droplevel()
df_2025 = df_2025.rename(columns={'count':'count_2025', 'mean':'mean_2025'})
df_2019.columns = df_2019.columns.droplevel()
df_2019 = df_2019.rename(columns={'count':'count_2019', 'mean':'mean_2019'})
df_summary = pd.concat([df_2025, df_2019], axis=1)

df_summary.loc[:,"delta_mean"] = df_summary["mean_2025"] - df_summary["mean_2019"]
df_summary.loc[:, "total_ct"] = df_summary["count_2025"] + df_summary["count_2019"]
df_summary = df_summary.reset_index()

#Keep only states with at least 50 entries
df_relevant = df_summary.loc[df_summary["total_ct"] > 50,:]
df_relevant.reset_index(drop=True, inplace=True)

#Add FIPS for each state so that it can be joined to later GeoJSON file as id
fips_list = pd.read_csv("fips.csv")
fips_list = fips_list.rename(columns={'State':'full_state', 'Postal':'state', 'FIPS':'id'})
df_relevant = pd.merge(df_relevant, fips_list, on='state', how='left')

#Get percent change between 2019 to 2025
#Technically not in percent here; will be changed to that within alt air
df_relevant.loc[:,"perc_delta_mean"] = (df_relevant["mean_2025"] - df_relevant["mean_2019"])/df_relevant["mean_2019"]

In [4]:
#Plotting the choropleth and a bar plot of states with highest percent increase 

usshapes = 'https://cdn.jsdelivr.net/npm/vega-datasets@v1.29.0/data/us-10m.json' #Load in USA
states = alt.topo_feature(usshapes, 'states')
us_base = alt.Chart(states).mark_geoshape(fill='#cccccc', stroke='black', strokeWidth=0.5)

chart = alt.Chart(states).mark_geoshape(stroke='black').encode(
    alt.Color('perc_delta_mean:Q', legend=alt.Legend(format="%", title='% Change in Mean Price', orient="right")).scale(domain=[min(df_relevant["perc_delta_mean"]), 0.0, max(df_relevant["perc_delta_mean"])], range=['dodgerblue',"white", "maroon"]
)).transform_lookup(
    lookup='id', #'id' being the FIPS that I merged in
    from_=alt.LookupData(df_relevant, 'id', ['perc_delta_mean'])
).properties(
    width=500,
    height=300,
    title=alt.TitleParams(text = "Percent Change in Mean Price by State from 2019 to 2025",
    subtitle = "States with over 50 total listings considered")
).project(type = 'albersUsa')

bar1 = alt.Chart(df_relevant).mark_bar(color='grey').transform_window(
    Rank='rank()',
    sort=[alt.SortField('perc_delta_mean', order='descending')]
).transform_filter(
    'datum.Rank < 10'
).encode(
    alt.X('perc_delta_mean:Q', axis=alt.Axis(format = "%", title = 'Increase in Mean Price')),
    alt.Y('state:N',  sort=alt.EncodingSortField(
        field='perc_delta_mean', order='descending'), axis=alt.Axis(title = 'State'))
).properties(title=alt.TitleParams(
        text='States with Greatest Increase in Mean Price Between 2019 and 2025'))

alt.vconcat(us_base+chart, bar1)

alt.VConcatChart(...)

# Address Suffix Comparison (Text Analysis)

In [5]:
#Separate analysis (not shown) found that, while some entries within the 2019 data included descriptions
#within the column "body" that listed the address, there was too much variability within the descriptions
#provided (since some might have addresses while others give long lists of ammenitites)
#and it was determined it would be too difficult to ascertain which of these contain addresses and corresponding suffixes
#there are a lot of possible suffixes with USPS (e.g. "IS" is a possible abbreviation for the suffix "Island" but the word "is" 
#appears in most apartment descriptions)
#So, analysis only included entries with a clear address available, which was ~80% of all the data, which was deemed acceptable

#Standardize address column
df_all.loc[:,"new_address"] = df_all["address"].str.upper()

#Which entries are NA addresses
sum_na = [False]*df_all.shape[0]
for i in range(0,df_all.shape[0]):
    if df_all.loc[i,"address"] is np.nan:
        sum_na[i] = True
        
#Keep only entries that are not NA addresses
df_address = df_all.loc[~pd.Series(sum_na),:]
df_address.reset_index(drop=True, inplace=True)

#Load in list of possible postal suffixes
#https://pe.usps.com/text/pub28/28apc_002.htm
postal_codes = pd.read_csv("postal_code_options.csv")

#First column is the full suffix, along with commonly used abbreviations, as listed by USPS
#Second column is then the standard suffix abbreviation that we want to use

df_address.loc[:,"postal_code"] = "" #Initialize column for postal suffixes

for i in range(0,df_address.shape[0]):
    #See if address includes at least one suffix, since some entries miss this information
    if len(postal_codes["postal_code"].loc[postal_codes["postal_options"].isin(df_address.loc[i,"new_address"].split(" "))]) > 0:
        last_entry_index = len(postal_codes["postal_code"].loc[postal_codes["postal_options"].isin(df_address.loc[i,"new_address"].split(" "))])-1
        df_address.loc[i,"postal_code"] = postal_codes["postal_code"].loc[postal_codes["postal_options"].isin(df_address.loc[i,"new_address"].split(" "))].iloc[last_entry_index]
        #Note: Take last match to a postal code
        #If there are more than 1 match, this ususally is because the word "AVENUE" technically contains the two frequent
        #suffixes used of AVENUE and AVE, so it gets matches twice, but selecting either match gives the standardized "AVE" output we want
        #Another issue that could occur is the fact that WEST is frequently used within an address, but it is not the suffix
        #However, the suffix "ST" would be incorrectly identified in this string and listed as a matched suffix.
        #So, the last entry is used, since it is assumed that any descriptors like West should be listed before the final address suffix
        
#Remove entries that did not have a suffix available in the address
df_address = df_address.loc[df_address["postal_code"] != "",:]
df_address.reset_index(drop=True, inplace=True) #At this point, 70% of all entries

In [6]:
#Get count of each suffix type by year
street_year_df = df_address.groupby(["postal_code","year"]).agg("count")
street_year_df = street_year_df.loc[:,"id"]
street_year_df = street_year_df.reset_index()
#Get total count per year
street_year_df.loc[:,"sum_id"] = [street_year_df.groupby("postal_code").agg("sum").loc[item,"id"] for item in street_year_df["postal_code"]]

#Keep only suffixes with at least 100 total entries
keep_streets = list(set(street_year_df.loc[street_year_df["sum_id"] >= 100,"postal_code"]))
df_address_keep = df_address.loc[df_address["postal_code"].isin(keep_streets),:]

In [7]:
step = 20
overlap = 1

plt1 = alt.layer(alt.Chart(df_address_keep, height=step).transform_filter(
    'datum.year == 2019'
).transform_density(
    'price', as_= ["price", "Density"],
    groupby=['postal_code','year']
).mark_area(
    interpolate='monotone',
    fillOpacity=0.8,
    stroke='lightgray',
    strokeWidth=0.5
).encode(
    alt.X('price:Q', scale=alt.Scale(domain=[0, 5000]))
        .title('Price'),
    alt.Y('Density:Q', scale=alt.Scale(domain=[0, 1]))
        .axis(None)
        .scale(range=[step, -step * overlap]),
    alt.Fill('postal_code:N', scale=alt.Scale(scheme='category20'))
),
          
    alt.Chart(df_address_keep, height=step).transform_filter(
    'datum.year == 2019'
).mark_rule(
    color="black").encode(
    alt.X("mean(price):Q", scale=alt.Scale(domain=[0, 5000])),
    size=alt.value(1),
)).facet(
    row=alt.Row('postal_code:N')
        .title(None)
        .header(labelAngle=0, labelAlign='left'),
    spacing={'row': 0}
).properties(
    title='Price Distributions by Address Suffixes, 2019',
    bounds='flush'
)
    

plt2 = alt.layer(alt.Chart(df_address_keep, height=step).transform_filter(
    'datum.year == 2025'
).transform_density(
    'price', as_= ["price", "Density"],
    groupby=['postal_code','year']
).mark_area(
    interpolate='monotone',
    fillOpacity=0.8,
    stroke='lightgray',
    strokeWidth=0.5
).encode(
    alt.X('price:Q', scale=alt.Scale(domain=[0, 5000]))
        .title('Price'),
    alt.Y('Density:Q', scale=alt.Scale(domain=[0, 1]))
        .axis(None)
        .scale(range=[step, -step * overlap]),
    alt.Fill('postal_code:N', scale=alt.Scale(scheme='category20'), legend=None)
),
          
    alt.Chart(df_address_keep, height=step).transform_filter(
    'datum.year == 2025'
).mark_rule(
    color="black").encode(
    alt.X("mean(price):Q", scale=alt.Scale(domain=[0, 5000])),
    size=alt.value(1),
)).facet(
    row=alt.Row('postal_code:N')
        .title(None)
        .header(labelAngle=0, labelAlign='left'),
    spacing={'row': 0}
).properties(
    title='Price Distributions by Address Suffixes, 2025',
    bounds='flush'
)

alt.vconcat(plt1, plt2).resolve_scale(
    y='shared'
)

alt.VConcatChart(...)